The aim of this notebook is to aid you in visualizing how polarization vectors rotate as a function of time based on the choice of moduli and phase shifts. If your notebook gets corrupted, don't worry, simply download a new version or restart it on Colab or Binder.

# Preliminaries

Begin by carrying out some preliminary steps.  Once these are done, they do not need to be repeated.

Install and import necessary packages.

In [1]:
import sys
!{sys.executable} -m pip install --quiet matplotlib

import matplotlib.pyplot as plt
import numpy as np
from matplotlib import animation
from IPython.display import HTML

Next, create a set of arrays to hold the history of polarization vector tip locations.

In [2]:
xp, yp, xm, ym, x1, y1 = ([] for i in range(6))

Define the routine to plot the circular polarization vectors and their histories.

In [3]:
def circular(ax, i, w, theta, a_plus, a_minus, chi):
    dxp = a_plus * np.cos(theta[i] + chi) / np.sqrt(2)
    dyp = a_plus * np.sin(theta[i] + chi) / np.sqrt(2)
    dpxf = dxp / (dxp**2 + dyp**2)**(1./2.)
    dpyf = dyp / (dxp**2 + dyp**2)**(1./2.)

    dxm = a_minus * np.cos(theta[i] - chi) / np.sqrt(2)
    dym = -a_minus * np.sin(theta[i] - chi) / np.sqrt(2)
    dmxf = dxm / (dxm**2 + dym**2)**(1./2.)
    dmyf = dym / (dxm**2 + dym**2)**(1./2.)
    
    ax.arrow(x = 0, y = 0, dx = dxp, dy = dyp, head_width = w, head_length = w, fc = 'red', ec = 'red')
    ax.arrow(x = 0, y = 0, dx = dxm, dy = dym, head_width = w, head_length = w, fc = 'green', ec = 'green')
    
    xp.append(dxp+w*dpxf)
    yp.append(dyp+w*dpyf)
    xm.append(dxm+w*dmxf)
    ym.append(dym+w*dmyf)

    ax.plot(xp, yp, ':', color = 'red')
    ax.plot(xm, ym, ':', color = 'green')

Now, define the routine to draw a frame of the animation.

In [4]:
def updatefig(i, a_plus, a_minus, alpha_plus, alpha_minus, theta, w, b_linear, b_circular):
    ax.cla()
    
    if i == 0:
        for tx in xp, yp, xm, ym, x1, y1:
            tx.clear()
    
    major = (a_minus + a_plus) / np.sqrt(2.)
    minor = (a_minus - a_plus) / np.sqrt(2.)
    chi = 0.5 * (alpha_minus - alpha_plus)
        
    dx1 = major * np.cos(theta[i])*np.cos(chi) + minor * np.sin(theta[i])*np.sin(chi)
    dy1 = -minor * np.sin(theta[i])*np.cos(chi) + major * np.cos(theta[i])*np.sin(chi)
    
    if b_linear:
        ax.arrow(x = 0, y = 0, dx = dx1, dy = 0, head_width = w, head_length = w, fc = 'blue', ec = 'blue')
        ax.arrow(x = 0, y = 0, dx = 0, dy = dy1, head_width = w, head_length = w, fc = 'orange', ec = 'orange')

    ax.arrow(x = 0, y = 0, dx = dx1, dy = dy1, head_width = w, head_length = w, fc = 'black', ec = 'black')
    
    if b_circular:
        circular(ax, i, w, theta, a_plus, a_minus, chi)
    
    dxf = dx1 / (dx1**2 + dy1**2)**(1./2.)
    dyf = dy1 / (dx1**2 + dy1**2)**(1./2.)

    x1.append(dx1+w*dxf)
    y1.append(dy1+w*dyf)
    
    ax.plot(x1, y1, ':', color = 'black')

    l = 1.2 * major
    ax.set(xlim=(-l, l), ylim=(-l, l))

# Polarization Calculation

With these preliminaries done, one can now set the polarization parameters.  *a_plus* and *a_minus* are the positive and negative circular polarization vector moduli, respectively, and *alpha_plus* and *alpha_minus* are the corresponding phase shifts.

In [5]:
a_plus = 2.5
a_minus = 1
alpha_plus = np.pi / 3
alpha_minus = 0

Set plot parameters to choose output for the display.  The animation will show the linear polarization vectors if *b_linear* is set to True and the circular polarization vectors if *b_circular* is set to True.  w sets the size of the head of the polarization vector. *n_cycles* is the number of cycles shown, and *n_frames_per_cycle* is the number of frames shown per cycle.

In [6]:
b_linear = False
b_circular = True
w = 0.1
n_cycles = 2
n_frames_per_cycle = 100

Now, create and display the animation.  

In [7]:
fig, ax = plt.subplots(figsize=(6, 6))
theta = np.linspace(0, n_cycles * 2 * np.pi, n_cycles * n_frames_per_cycle)

args = (a_plus, a_minus, alpha_plus, alpha_minus, theta, w, b_linear, b_circular)
anim = animation.FuncAnimation(fig, updatefig, fargs = args, frames=len(theta), blit=False)
plt.close() # prevents printing out 2 figures
HTML(anim.to_jshtml())

To try a new calculation, change the *a_plus*, *a_minus*, *alpha_plus*, and *alpha_minus* parameters, update the plot parameters (if desired), and generate a new animation.